# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [35 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
from google.colab import drive
drive.mount('/content/drive')

%cd /content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis/
%ls

Mounted at /content/drive
/content/drive/MyDrive/DAI-Labor/RL_VPP_Thesis
Agent_trainer_notebooks/          __pycache__/          VPP_environment.py
data/                             README.md             VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  Simulator_notebooks/  wandb/
log.log                           trained_models/


In [3]:
# #Cloning repository and changing directory
# !git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
# %cd RL_VPP_Thesis/
# %ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f220235e650>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 30
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 30, 'EVs_n_max': 1566, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  31549.47 , over-consume=kWh  46807.45 , under-consume=kWh  15257.98 , Total_cost=€  1182.62 , overcost=€  1630.33 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  30386.38 , over-consume=kWh  46191.73 , under-consume=kWh  15805.36 , Total_cost=€  1183.1 , overcost=€  1627.9 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  66.72
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2133.3 , over-consume=KWh  1215.56 , under-consume=KWh  3348.87 , Total_cost=€  -34.56 , Overcost=€  39.56 
 EV_INFO: Av.EV_energy_leaving=kWh  62.65 , Std.EV_energy_leaving=kWh  23.88 , EV_departures =  1563 , EV_queue_left =  2
SCORE:  Cumulative_reward= 471379.98 - Step_rewars (load_t= 433227.07, EVs_energy_t= 2984.1)
 - Final_rewards (EVs_energy= 20266.91, Overconsume= -257.78, Underconsume= -222.78, Overcost= 15382.46)
Episode:1 Score:471379.98130779096


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  42.376911  37.032276  54.814068  57.536682   
2022-01-01 00:15:00  42.626911  36.293701  54.075493  57.786682   
2022-01-01 00:30:00  42.876911  35.801083  53.582874  58.036682   
2022-01-01 00:45:00  43.126911  35.328064  53.109856  58.286682   
2022-01-01 01:00:00  43.376911  34.892616  52.674408  58.536682   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  99.989998   0.000000   0.000000  86.559471   
2022-06-06 05:00:00  99.989998   0.000000   0.000000  87.507622   
2022-06-06 05:15:00  99.989998   0.000000   0.000000  88.485329   
2022-06-06 05:30:00  99.989998   0.000000   0.000000  89.445496   
2022-06-06 05:45:00  99.989998   0.000000   0.000000  90.487579   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [4695, 4692, 4693, 4694]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [4695, 4692, 4693, 4694]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [4695, 4692, 4693, 4694]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [4695, 4692, 4693, 4694]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00        [5377, 0, 0, 5378]  [1, 1, 2, 1]   
2022-06-06 05:00:00        [5377, 0, 0, 5378]  [1, 1, 2, 1]   
2022-06-06 05:15:00        [5377, 0, 0, 5378]  [1, 1, 2, 1]   
2022-06-06 05:30:00        [5377, 0, 0, 5378]  [1, 1, 2, 1]   
2022-06-06 05:45:00        [5377, 0, 0, 5378]  [1, 1, 2, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.129140e+00    15.000000   
2022-01-01 00:15:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 00:30:00    [False, True, True, False]  2.220446e-16    15.000000   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [False, True, True, False]  2.220446e-16    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00   [False, False, False, True] -5.683472e+00    -8.259267   
2022-06-06 05:00:00   [False, False, False, True] -7.585193e+00    -8.474239   
2022-06-06 05:15:00   [False, False, False, True] -7.821663e+00    -8.346684   
2022-06-06 05:30:00   [False, False, False, True] -7.681352e+00    -8.942394   
2022-06-06 05:45:00   [False, False, False, True] -8.336634e+00    -8.233555   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -8.259267  
2022-06-06 05:00:00        0.0  -8.474239  
2022-06-06 05:15:00        0.0  -8.346684  
2022-06-06 05:30:00        0.0  -8.942394  
2022-06-06 05:45:00        0.0  -8.233555  

[15000 rows x 11 columns]

In [25]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_Elvis_comparison()

In [28]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [29]:
env.plot_rewards_stats()

In [30]:
env.plot_EVs_kpi()

In [31]:
env.plot_load_kpi()

In [32]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [33]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6261, Arrival time: 2022-01-01 06:15:00, Parking_time: 23.60412470727449, Leaving_time: 2022-01-02 05:51:14.848946, SOC: 0.536435503837688, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7825, Arrival time: 2022-12-31 11:30:00, Parking_time: 24, Leaving_time: 2023-01-01 11:30:00, SOC: 0.2347611179766636, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  23375.24 , over-consume=kWh  43367.22 , under-consume=kWh  19991.98 , Total_cost=€  1069.87 , overcost=€  1891.44 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59


In [34]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [35]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [36]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22588.18 , over-consume=kWh  42879.18 , under-consume=kWh  20291.0 , Total_cost=€  1039.11 , overcost=€  1871.51 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.59
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3462.01 , over-consume=KWh  817.23 , under-consume=KWh  4279.24 , Total_cost=€  -110.81 , Overcost=€  35.66 
 EV_INFO: Av.EV_energy_leaving=kWh  66.9 , Std.EV_energy_leaving=kWh  23.55 , EV_departures =  1559 , EV_queue_left =  2
SCORE:  Cumulative_reward= 492145.0 - Step_rewars (load_t= 425928.21, EVs_energy_t= 26268.25)
 - Final_rewards (EVs_energy= 22831.56, Overconsume= 941.1, Underconsume= -204.25, Overcost= 16380.13)
Episode:1 Score:492145.0011465347


In [37]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [38]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  72.580833  49.673622  48.655807  80.198349   
2022-06-06 05:00:00  73.464012  50.556805  49.538990  81.081528   
2022-06-06 05:15:00  74.314972  51.407768  50.389954  81.932487   
2022-06-06 05:30:00  75.129593  52.222393  51.204578  82.747108   
2022-06-06 05:45:00  75.927933  53.020729  52.002914  83.545448   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [10020, 10022, 10021, 10019]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [10020, 10022, 10021, 10019]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [10020, 10022, 10021, 10019]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [10020, 10022, 10021, 10019]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [10020, 10022, 10021, 10019]  [1, 1, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -4.170726    -4.827000   
2022-01-01 00:15:00  [False, False, False, True] -3.896200    -5.673292   
2022-01-01 00:30:00  [False, False, False, True] -4.740622    -3.475039   
2022-01-01 00:45:00  [False, False, False, True] -3.085023    -5.353594   
2022-01-01 01:00:00   [False, True, False, True] -4.388953    -5.314100   
...                                          ...       ...          ...   
2022-06-06 04:45:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:00:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:15:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:30:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:45:00     [True, True, True, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.827000  
2022-01-01 00:15:00        0.0  -5.673292  
2022-01-01 00:30:00        0.0  -3.475039  
2022-01-01 00:45:00        0.0  -5.353594  
2022-01-01 01:00:00        0.0  -5.314100  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [39]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [40]:
env.plot_VPP_Elvis_comparison()

In [41]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_rewards_stats()

In [43]:
env.plot_EVs_kpi()

In [44]:
env.plot_load_kpi()

In [45]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [46]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 10956, Arrival time: 2022-01-01 05:45:00, Parking_time: 23.31941453527384, Leaving_time: 2022-01-02 05:04:09.892327, SOC: 0.5162101573163745, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 12520, Arrival time: 2022-12-31 21:00:00, Parking_time: 24, Leaving_time: 2023-01-01 21:00:00, SOC: 0.43511749002228356, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18404.21 , over-consume=kWh  39444.16 , under-consume=kWh  21039.95 , Total_cost=€  875.15 , overcost=€  1646.73 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79


In [47]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [48]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [49]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18506.7 , over-consume=kWh  39202.11 , under-consume=kWh  20695.41 , Total_cost=€  849.22 , overcost=€  1615.4 , Av.EV_en_left=kWh  100.0 , Charging_events=  1565 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  72.79
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4275.97 , over-consume=KWh  608.69 , under-consume=KWh  4884.66 , Total_cost=€  -143.18 , Overcost=€  25.48 
 EV_INFO: Av.EV_energy_leaving=kWh  69.26 , Std.EV_energy_leaving=kWh  23.13 , EV_departures =  1561 , EV_queue_left =  0
SCORE:  Cumulative_reward= 500943.17 - Step_rewars (load_t= 418776.0, EVs_energy_t= 37564.77)
 - Final_rewards (EVs_energy= 23801.22, Overconsume= 4473.03, Underconsume= -675.49, Overcost= 17003.64)
Episode:1 Score:500943.17116313527


In [50]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [51]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  55.301876   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  56.510235   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  46.387127  57.061749  54.432095  70.409348   
2022-06-06 03:45:00  47.144482  56.811749  52.943626  71.166702   
2022-06-06 04:00:00  48.158310  56.561749  52.693626  72.180527   
2022-06-06 04:15:00  48.765411  56.311749  53.300728  72.787628   
2022-06-06 04:30:00  49.455315  56.061749  53.990631  73.477531   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 14086, 0, 0]  [0, 1, 2, 2]   
2022-01-01 01:00:00              [0, 14086, 0, 0]  [0, 1, 2, 2]   
...                                           ...           ...   
2022-06-06 03:30:00  [14774, 14772, 14771, 14773]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [14774, 14772, 14775, 14773]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [14774, 14772, 14775, 14773]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [14774, 14772, 14775, 14773]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [14774, 14772, 14775, 14773]  [1, 2, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, False, False, True] -3.784682e+00    -4.227724   
2022-01-01 00:15:00  [False, False, False, True] -3.536634e+00    -2.552369   
2022-01-01 00:30:00  [False, False, False, True] -2.531421e+00    -3.246262   
2022-01-01 00:45:00   [True, True, False, False] -2.947757e+00    15.000000   
2022-01-01 01:00:00   [True, True, False, False]  0.000000e+00    15.000000   
...                                          ...           ...          ...   
2022-06-06 03:30:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 03:45:00   [True, False, False, True]  0.000000e+00    15.000000   
2022-06-06 04:00:00    [True, False, True, True]  8.881784e-16    15.000000   
2022-06-06 04:15:00    [True, False, True, True]  0.000000e+00    15.000000   
2022-06-06 04:30:00    [True, False, True, True]  0.000000e+00    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00   0.000000  -4.227724  
2022-01-01 00:15:00   0.000000  -2.552369  
2022-01-01 00:30:00   0.000000  -3.246262  
2022-01-01 00:45:00   0.000000  15.000000  
2022-01-01 01:00:00   0.000000  15.000000  
...                        ...        ...  
2022-06-06 03:30:00 -20.135051  -5.135051  
2022-06-06 03:45:00   0.000000  15.000000  
2022-06-06 04:00:00   0.000000  15.000000  
2022-06-06 04:15:00   0.000000  15.000000  
2022-06-06 04:30:00   0.000000  15.000000  

[14995 rows x 11 columns]

In [52]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
env.plot_VPP_Elvis_comparison()

In [54]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_rewards_stats()

In [56]:
env.plot_EVs_kpi()

In [57]:
env.plot_actions_kpi()

In [58]:
env.plot_load_kpi()

In [59]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [60]:
#env.close()